In [3]:
import pandas as pd

In [5]:
df_2024 = pd.read_csv("../data/final_game_logs_2024.csv")
df_2025 = pd.read_csv("../data/final_game_logs_2025.csv")
games_2024 = pd.read_csv("../data/game_logs_2024.csv")
games_2025 = pd.read_csv("../data/game_logs_2025.csv")

In [7]:
games_2024["game_date"] = pd.to_datetime(games_2024["game_date"])
games_2025["game_date"] = pd.to_datetime(games_2025["game_date"])

In [11]:
games_2024.head(2)

game_id         game_datetime  game_date game_type status  \
0   748266  2024-02-22T20:10:00Z 2024-02-22         S  Final   
1   748344  2024-02-23T18:05:00Z 2024-02-23         E  Final   

              away_name         home_name  away_id  home_id doubleheader  ...  \
0   Los Angeles Dodgers  San Diego Padres      119      135            N  ...   
1  Northeastern Huskies    Boston Red Sox      343      111            N  ...   

       venue_name           national_broadcasts  series_status  \
0  Peoria Stadium  ['ESPN', 'MLB.tv Free Game']  LAD leads 1-0   
1    JetBlue Park                            []            NaN   

          winning_team           losing_team  winning_pitcher  losing_pitcher  \
0  Los Angeles Dodgers      San Diego Padres      Gavin Stone    Joe Musgrove   
1       Boston Red Sox  Northeastern Huskies    Chase Shugart   Joseph Hauser   

   save_pitcher                                            summary  \
0           NaN  2024-02-22 - Los Angeles Dodgers (14) @ San Di...   
1           NaN  2024-02-23 - Northeastern Huskies (2) @ Boston...   

   losing_Team  
0          NaN  
1          NaN  

[2 rows x 30 columns]

In [17]:
df_2024.columns

Index(['game_id', 'home_name', 'away_name', 'home_probable_pitcher',
       'away_probable_pitcher', 'away_score', 'home_score', 'home_ERA',
       'home_ER', 'home_R', 'home_SO', 'home_BB', 'home_SO/BB', 'home_WHIP',
       'away_ERA', 'away_ER', 'away_R', 'away_SO', 'away_BB', 'away_SO/BB',
       'away_WHIP', 'home_OBP', 'home_SLG', 'home_HR', 'home_R/G',
       'home_BB_batting', 'home_SO_batting', 'home_IBB', 'away_OBP',
       'away_SLG', 'away_HR', 'away_R/G', 'away_BB_batting', 'away_SO_batting',
       'away_IBB', 'temp', 'condition', 'wind', 'home_lineup_score',
       'away_lineup_score', 'home_n_starters', 'away_n_starters',
       'home_last7_win_pct', 'home_streak', 'away_last7_win_pct',
       'away_streak', 'Partly Cloudy', 'Clear', 'Sunny', 'Cloudy',
       'Roof Closed', 'Overcast', 'Dome', 'Drizzle', 'Unknown', 'Rain'],
      dtype='object')

In [53]:
def compute(games_df, final_df):
    games_df = games_df.sort_values("game_date")

    def get_team_history(team, date):
        return games_df[((games_df["home_name"] == team) | (games_df["away_name"] == team)) & (games_df["game_date"] < date)]
        
    def winrate_streak(team, date):
        team_games = get_team_history(team,date)
        if len(team_games) == 0:
            return None, None

        team_games["team_win"] = (
            ((team_games["home_name"] == team) & (team_games["home_score"] > team_games["away_score"])) |
            ((team_games["away_name"] == team) & (team_games["away_score"] > team_games["home_score"]))
        ).astype(int)

        last7 = team_games["team_win"].tail(7)
        win_pct = last7.mean() if len(last7) > 0 else None
        reversed = team_games["team_win"].values[::-1]
        if len(reversed) == 0:
            return win_pct, None
        streak = 1 if reversed[0] == 1 else -1
        for res in reversed[1:]:
            if res == reversed[0]:
                streak += 1 if streak > 0 else -1
            else:
                break
        return win_pct, streak

    results = []
    for _, row in final_df.iterrows():
        home_team, away_team = row["home_name"], row["away_name"]
        game_date = pd.to_datetime(games_df[games_df["game_id"] == row["game_id"]]["game_date"].iloc[0])
        home_last7_win_pct, home_streak = winrate_streak(home_team, game_date)
        away_last7_win_pct, away_streak = winrate_streak(away_team, game_date)
        results.append((home_last7_win_pct, home_streak, away_last7_win_pct, away_streak))
    final_df[["home_last7_win_pct", "home_streak", "away_last7_win_pct", "away_streak"]] = results
    return final_df

In [55]:
df_2024 = compute(games_2024, df_2024)
df_2025 = compute(games_2025, df_2025)

/var/folders/k2/hmwmh0zn7_39kx03c2fbhh500000gn/T/ipykernel_71928/3933164818.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["team_win"] = (
/var/folders/k2/hmwmh0zn7_39kx03c2fbhh500000gn/T/ipykernel_71928/3933164818.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  team_games["team_win"] = (
/var/folders/k2/hmwmh0zn7_39kx03c2fbhh500000gn/T/ipykernel_71928/3933164818.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

In [57]:
df_2025[(df_2025["home_name"] == "Los Angeles Dodgers") | (df_2025["away_name"] == "Los Angeles Dodgers")][["home_streak", "away_streak"]]

home_streak  away_streak
0             NaN          NaN
3             1.0         -1.0
16           -2.0          1.0
33           -3.0          2.0
40           -2.0          1.0
...           ...          ...
2473          2.0         -1.0
2486          3.0         -2.0
2510          4.0          2.0
2525         -1.0          3.0
2540         -2.0          4.0

[162 rows x 2 columns]

In [51]:
df_2025[(df_2025["home_name"] == "Los Angeles Dodgers") | (df_2025["away_name"] == "Los Angeles Dodgers")]

game_id            home_name             away_name  \
0      778869  Los Angeles Dodgers          Chicago Cubs   
3      778760         Chicago Cubs   Los Angeles Dodgers   
16     778867  Los Angeles Dodgers    Kansas City Royals   
33     778864  Los Angeles Dodgers      San Diego Padres   
40     778837      Cincinnati Reds   Los Angeles Dodgers   
...       ...                  ...                   ...   
2473   776574  Los Angeles Dodgers       Cincinnati Reds   
2486   776562  Los Angeles Dodgers       Cincinnati Reds   
2510   776534  Los Angeles Dodgers  Arizona Diamondbacks   
2525   776523  Los Angeles Dodgers  Arizona Diamondbacks   
2540   776509  Los Angeles Dodgers  Arizona Diamondbacks   

     home_probable_pitcher away_probable_pitcher  away_score  home_score  \
0       Yoshinobu Yamamoto           Cody Poteet          12           4   
3             Jordan Wicks         Tony Gonsolin           3           7   
16             Nick Frasso    Chandler Champlain          11          10   
33              Dustin May           Braden Nett           3           8   
40            Brady Singer         Tyler Glasnow           1           8   
...                    ...                   ...         ...         ...   
2473       Clayton Kershaw         Nick Martinez           3           6   
2486         Shohei Ohtani           Nick Lodolo           1           5   
2510           Blake Snell            Zac Gallen           3           0   
2525         Tyler Glasnow     Eduardo Rodriguez           6           1   
2540    Yoshinobu Yamamoto        Brandon Pfaadt           4           5   

      home_ERA  home_ER  home_R  ...  Clear  Sunny  Cloudy  Roof Closed  \
0         2.49     48.0    53.0  ...  False   True   False        False   
3         6.28     10.0    12.0  ...  False   True   False        False   
16         NaN      NaN     NaN  ...  False   True   False        False   
33        4.96     73.0    78.0  ...  False  False   False        False   
40        4.03     76.0    80.0  ...  False  False   False        False   
...        ...      ...     ...  ...    ...    ...     ...          ...   
2473      3.36     42.0    46.0  ...   True  False   False        False   
2486      2.87     15.0    15.0  ...   True  False   False        False   
2510      2.35     16.0    21.0  ...   True  False   False        False   
2525      3.19     32.0    33.0  ...   True  False   False        False   
2540      2.49     48.0    53.0  ...  False   True   False        False   

      Overcast   Dome  Drizzle  Unknown   Rain  away_strea  
0        False  False    False    False  False         NaN  
3        False  False    False    False  False        -1.0  
16       False  False    False    False  False         1.0  
33       False  False    False    False  False         2.0  
40       False  False    False    False  False         1.0  
...        ...    ...      ...      ...    ...         ...  
2473     False  False    False    False  False        -1.0  
2486     False  False    False    False  False        -2.0  
2510     False  False    False    False  False         2.0  
2525     False  False    False    False  False         3.0  
2540     False  False    False    False  False         4.0  

[162 rows x 57 columns]

In [61]:
df_2024.to_csv("../data/final_game_logs_2024.csv", index=False)
df_2025.to_csv("../data/final_game_logs_2025.csv", index=False)